In [ ]:
import math
import numpy as np
import torch
import random

In [ ]:
with np.load('imdb.npz') as f:
    trX = f['x_train']
    trY = f['y_train']
    teX = f['x_test']
    teY = f['y_test']

In [ ]:
def remove_rare_words(dataset, cutoff):
    for i, x in enumerate(dataset):
        x_new = []
        for word in x:
            if word <= cutoff:
                x_new.append(word)
        dataset[i] = x_new
    return dataset

trX = remove_rare_words(trX, 10000)
teX = remove_rare_words(teX, 10000)

In [ ]:
def transform_dataset(trX, max_len):
    X = np.zeros((len(trX), max_len))
    
    # Insert code here
    # X[i] should be trX[i], but fixed length max_len (either cap trX[i] or add zeros
    
    return X

trX = transform_dataset(trX, 500)
teX = transform_dataset(teX, 500)

In [ ]:
trX = torch.tensor(trX).long()
trY = torch.tensor(trY).float()
teX = torch.tensor(teX).long()
teY = torch.tensor(teY).float()

perm = torch.randperm(len(trX))
trX, trY = trX[perm], trY[perm]

In [ ]:
class Network(torch.nn.Module):
    def __init__(self):
        super(Network, self).__init__()
        self.embedding = torch.nn.Embedding(10001, 64)
        
        # Insert code here
        # add layers, for example  self.conv1 = torch.nn.Conv1d(64,64,5,1,2)
        # convolution arguments are: input channels, output channels, kernel size, stride and padding
        
    def forward(self, x):
        x = self.embedding(x)
        
        # Insert code here
        # run your model, for example x = self.conv1(x)

        return x

model = Network()
if torch.cuda.is_available(): 
    print("Using cuda")
    model = model.cuda()

criterion = torch.nn.BCELoss()
optimizer = torch.optim.RMSprop(model.parameters())

In [ ]:
batch_size = 128
model.train()

for epoch in range(20):
    num_correct = 0
    for batch_idx in range(len(trX)//batch_size):
        start, end = batch_size*batch_idx, batch_size*(batch_idx+1)
        
        x,y = trX[start:end], trY[start:end]
        if torch.cuda.is_available():
            x, y = x.cuda(), y.cuda()
            
        output = model(x).view(-1)
        loss = criterion(output, y)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        num_correct += ((output > .5) == y.byte()).sum().item()
    print("Epoch:%s  | Train acc: %s"%(epoch, num_correct/len(trY)))  

In [ ]:
with torch.no_grad():
    num_correct = 0
    for batch_idx in range(len(teX)//batch_size):
        start, end = batch_size*batch_idx, batch_size*(batch_idx+1)

        x,y = teX[start:end], teY[start:end]
        if torch.cuda.is_available():
            x, y = x.cuda(), y.cuda()

        output = model(x).view(-1)
        num_correct += ((output > .5) == y.byte()).sum().item()
    print("Test acc: %s"%(num_correct/len(trY)))  